In [1]:
import copy
import pandas as pd
import numpy as np
import warnings
warnings.filterwarnings("ignore")
from sklearn.preprocessing import StandardScaler
from sklearn.svm import SVR
from sklearn.ensemble import RandomForestRegressor
from sklearn.linear_model import LinearRegression, Lasso, SGDRegressor
from sklearn.neural_network import MLPRegressor
from nnpredmine import nn_train, nn_pred, nn_finetune
from utils import  MAPE, MAE

In [2]:
import os 
os.environ['CUDA_VISIBLE_DEVICES'] = '0'

In [3]:
city_list =['Perth', 'HK', 'PALO', 'DUNDEE', 'BOULDER','Auchterarder','Kinross','Pitlochry','Crieff','Aberfeldy','Dunkeld','Blairgowrie']
city_num = 12

data_list = []
file_list = [
    './Data/STATION/A1-PERTH.csv',
    './Data/STATION/A2-XIANGGANG.csv',
    './Data/STATION/A3-PALO.csv',
    './Data/STATION/A4-DUNDEE.csv',
    './Data/STATION/A5-BOULDER.csv',
    './Data/STATION/A6-Auchterarder.csv',
    './Data/STATION/A7-Kinross.csv',
    './Data/STATION/A8-Pitlochry.csv',
    './Data/STATION/A9-Crieff.csv',
    './Data/STATION/A10-Aberfeldy.csv',
    './Data/STATION/A11-Dunkeld.csv',
    './Data/STATION/A12-Blairgowrie.csv'
]

for file in file_list:

    data = pd.read_csv(file).values
    data_list.append(data[:,1:])
    
his_len = 12
pred_len = 1

In [4]:
def get_train_test (data, mode, his_len, pred_len, train_rate = 0.8):

    train_num = int(data.shape[0] * train_rate)
    XS, YS = [], []
    if mode == 'train':
        for i in range(train_num - pred_len - his_len + 1):
            x = data[i:i + his_len, :]
            y = data[i + his_len:i + his_len + pred_len, :]
            XS.append(x), YS.append(y)
    elif mode == 'test':
        for i in range(train_num - his_len,
                       data.shape[0] - pred_len - his_len + 1):
            x = data[i:i + his_len, :]
            y = data[i + his_len:i + his_len + pred_len, :]
            XS.append(x), YS.append(y)

    XS, YS = np.array(XS), np.array(YS)
    XS, YS = np.squeeze(XS), np.squeeze(YS)
    
    return XS, YS

In [5]:
# train test split
train_list = []
test_list = []
scaler_list = []
sensor_num_list = []

for data in data_list:

    scaler = StandardScaler()
    data = scaler.fit_transform(data)
    
    train_x, train_y = get_train_test (data, 'train', his_len, pred_len, train_rate = 0.8 )
    test_x, test_y = get_train_test (data, 'test', his_len, pred_len, train_rate = 0.8)

    sensor_num_list.append(data.shape[1])

    train_x = np.reshape(train_x, (-1, his_len))
    train_y = np.reshape(train_y, (-1, pred_len))
    test_x = np.reshape(test_x, (-1, his_len))
    test_y = np.reshape(test_y, (-1, pred_len))

    train_list.append([train_x, train_y])
    test_list.append([test_x, test_y])
    scaler_list.append(scaler)


In [6]:
for model_name in ['GRU','SGD','MLP','RF','LASSO',]:#'GRU','SGD','MLP','RF','LSTM','LASSO',#'LSTM',
    for transfer_day_len in [1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16,17,18,19,20,21,22,23,24]:
        print("transfer_day_len: ",transfer_day_len)

        # source, target, metric
        transfer_rec = np.zeros((city_num, city_num, 2))
        wo_transfer_rec = np.zeros((city_num, 2))

        for source_idx in range(city_num):
            # train on the source city
            print('-------------------------------')
            print('-------Source city: {:s}-------'.format(city_list[source_idx]))
            print('-------------------------------')

            source_x, source_y = train_list[source_idx]
            print(source_x.shape, source_y.shape)

            if model_name == 'RF':
                model = RandomForestRegressor(max_depth=2, random_state=0, warm_start=True)
                model.fit(source_x, source_y)
            elif model_name == 'MLP':
                model = MLPRegressor(random_state=0, warm_start=True)
                model.fit(source_x, source_y)
            elif model_name == 'LASSO':
                model = Lasso(random_state=0, warm_start=True)
                model.fit(source_x, source_y)
            elif model_name == 'SGD':
                model = SGDRegressor(random_state=0, warm_start=True)
                model.fit(source_x, np.mean(source_y, axis=1))
            elif model_name == 'LSTM' or model_name == 'GRU':
                model = nn_train(source_x, source_y, model_name, learning_rate=1e-2)

            else:
                pass

            # test on the source city
            test_x, test_y = test_list[source_idx]

            if model_name == 'RF' or model_name == 'MLP' or model_name == 'LASSO':
                pred_y = model.predict(test_x)
            elif model_name == 'SGD':
                pred_y = model.predict(test_x)
                pred_y = np.reshape(pred_y, (-1, 1))
                pred_y = pred_y.repeat(pred_len ,axis=1)
            elif model_name == 'LSTM' or model_name == 'GRU':
                pred_y = nn_pred(test_x, test_y, model)

            else:
                pass

            test_y = np.reshape(test_y, (-1, sensor_num_list[source_idx], pred_len))
            pred_y = np.reshape(pred_y, (-1, sensor_num_list[source_idx], pred_len))

            test_y = scaler_list[source_idx].inverse_transform(test_y.transpose(0,2,1))
            pred_y = scaler_list[source_idx].inverse_transform(pred_y.transpose(0,2,1))
            pred_y = np.around(pred_y.astype(np.float32))
            pred_y [pred_y < 0] = 0

            mape, mae = MAPE(test_y, pred_y), MAE(test_y, pred_y)

            print('Test MAPE: MAE: | {:.4f} | {:.4f}'.format(mape,  mae))

            transfer_rec[source_idx, source_idx, 0] = mape
            transfer_rec[source_idx, source_idx, 1] = mae 


            # transfer to other cities
            for target_idx in range(city_num):

                if target_idx == source_idx:
                    continue
                    
                print('-------Target city: {:s}--------'.format(city_list[target_idx]))


                ###################
                #transfer
                ###################
                source_model = copy.copy(model)

                target_x, target_y = train_list[target_idx]
                target_x = target_x[(-24 * transfer_day_len + his_len)*sensor_num_list[target_idx]:, ]
                target_y = target_y[(-24 * transfer_day_len + his_len)*sensor_num_list[target_idx]:, ]
                print(target_x.shape, target_y.shape)

                test_x, test_y = test_list[target_idx]

                # transfer train and test
                if model_name == 'RF' or model_name == 'MLP'  or model_name == 'LASSO':
                    source_model.fit(target_x, target_y)
                    pred_y = source_model.predict(test_x)

                elif model_name == 'SGD':
                    source_model.fit(target_x, np.mean(target_y, axis=1))
                    pred_y = source_model.predict(test_x)
                    pred_y = np.reshape(pred_y, (-1, 1))
                    pred_y = pred_y.repeat(pred_len ,axis=1)
                elif model_name == 'LSTM' or model_name == 'GRU':
                    source_model = nn_finetune(test_x, test_y, source_model)
                    pred_y = nn_pred(test_x, test_y, source_model)

                else:
                    pass

                test_y = np.reshape(test_y, (-1, sensor_num_list[target_idx], pred_len))
                pred_y = np.reshape(pred_y, (-1, sensor_num_list[target_idx], pred_len))
                test_y = scaler_list[target_idx].inverse_transform(test_y.transpose(0,2,1))
                pred_y = scaler_list[target_idx].inverse_transform(pred_y.transpose(0,2,1))
                pred_y = np.around(pred_y.astype(np.float32))
                pred_y [pred_y < 0] = 0

                mape, mae = MAPE(test_y, pred_y),  MAE(test_y, pred_y)

                print('Transfer Test MAPE: MAE: | {:.4f} | {:.4f}'.format(mape, mae))

                transfer_rec[source_idx, target_idx, 0] = mape
                transfer_rec[source_idx, target_idx, 1] = mae 


                ###################
                # with out transfer
                ###################
                test_x, test_y = test_list[target_idx]

                if model_name == 'RF':
                    wo_trans_model = RandomForestRegressor(max_depth=2, random_state=0)
                    wo_trans_model.fit(target_x, target_y)
                    pred_y = wo_trans_model.predict(test_x)

                elif model_name == 'MLP':
                    wo_trans_model = MLPRegressor(random_state=0)
                    wo_trans_model.fit(target_x, target_y)
                    pred_y = wo_trans_model.predict(test_x)

                elif model_name == 'LASSO':
                    wo_trans_model = MLPRegressor(random_state=0)
                    wo_trans_model.fit(target_x, target_y)
                    pred_y = wo_trans_model.predict(test_x)
                elif model_name == 'SGD':
                    wo_trans_model = SGDRegressor(random_state=0)
                    wo_trans_model.fit(target_x, np.mean(target_y, axis=1))
                    pred_y = wo_trans_model.predict(test_x)
                    pred_y = np.reshape(pred_y, (-1, 1))
                    pred_y = pred_y.repeat(pred_len ,axis=1)
                elif model_name == 'LSTM' or model_name == 'GRU':
                    wo_trans_model = nn_train(target_x, target_y, model_name, learning_rate=1e-2)
                    pred_y = nn_pred(test_x, test_y, wo_trans_model)

                else:
                    pass

                test_y = np.reshape(test_y, (-1, sensor_num_list[target_idx], pred_len))
                pred_y = np.reshape(pred_y, (-1, sensor_num_list[target_idx], pred_len))

                test_y = scaler_list[target_idx].inverse_transform(test_y.transpose(0,2,1))
                pred_y = scaler_list[target_idx].inverse_transform(pred_y.transpose(0,2,1))
                pred_y = np.around(pred_y.astype(np.float32))
                pred_y [pred_y < 0] = 0

                mape,  mae = MAPE(test_y, pred_y),MAE(test_y, pred_y)

                print('Wo Transfer Test MAPE:  MAE: | {:.4f}  | {:.4f}'.format(mape,  mae))

                wo_transfer_rec[target_idx, 0] = mape
                wo_transfer_rec[target_idx, 1] = mae 

        metric_list = ['mape', 'mae']

        for i in range(len(metric_list)):

            save_df = pd.DataFrame(transfer_rec[:,:,i], index = city_list, columns= city_list)
            save_df.index.name = 'source \ target'
            save_df.loc['wo_trans'] = wo_transfer_rec[:,i]

            save_df.to_csv('res1/' + model_name  + '_trans_' + str(transfer_day_len) + '_pred_' + str(pred_len) + '_' + metric_list[i] + '.csv')

transfer_day_len:  1
-------------------------------
-------Source city: Perth-------
-------------------------------
(3384, 12) (3384, 1)
Early stopping at epoch: 24
epoch 24 train loss: 0.8032968366634903 validation loss: 1.046059489250183
Test MAPE: MAE: | 0.2107 | 0.4039
-------Target city: HK--------
(120, 12) (120, 1)
Early stopping at epoch: 20
epoch 20 train loss: 1.0930886886737965 validation loss: 0.9192943572998047
Transfer Test MAPE: MAE: | 0.2007 | 0.4708
Early stopping at epoch: 22
epoch 22 train loss: 0.6012875437736511 validation loss: 1.5380504131317139
Wo Transfer Test MAPE:  MAE: | 0.2456  | 0.4569
-------Target city: PALO--------
(84, 12) (84, 1)
Early stopping at epoch: 46
epoch 46 train loss: 0.9021584391593933 validation loss: 1.5705492496490479
Transfer Test MAPE: MAE: | 0.6719 | 0.6300
Early stopping at epoch: 23
epoch 23 train loss: 0.8682462573051453 validation loss: 0.5994142293930054
Wo Transfer Test MAPE:  MAE: | 0.2931  | 0.8829
-------Target city: DUNDEE

Early stopping at epoch: 23
epoch 23 train loss: 0.9692805780120255 validation loss: 0.9960545301437378
Test MAPE: MAE: | 0.2547 | 0.8690
-------Target city: Perth--------
(72, 12) (72, 1)
Early stopping at epoch: 20
epoch 20 train loss: 0.6601715087890625 validation loss: 1.1629064083099365
Transfer Test MAPE: MAE: | 0.2121 | 0.4225
Early stopping at epoch: 22
epoch 22 train loss: 1.3811805248260498 validation loss: 1.0648589134216309
Wo Transfer Test MAPE:  MAE: | 0.2811  | 0.5891
-------Target city: HK--------
(120, 12) (120, 1)
Early stopping at epoch: 20
epoch 20 train loss: 1.0930111290496072 validation loss: 0.919673502445221
Transfer Test MAPE: MAE: | 0.2007 | 0.4708
Early stopping at epoch: 22
epoch 22 train loss: 0.6012875437736511 validation loss: 1.5380504131317139
Wo Transfer Test MAPE:  MAE: | 0.2456  | 0.4569
-------Target city: DUNDEE--------
(324, 12) (324, 1)
Early stopping at epoch: 79
epoch 79 train loss: 0.8383674825094023 validation loss: 1.7871711254119873
Transf

Early stopping at epoch: 26
epoch 26 train loss: 1.076706466806085 validation loss: 1.0638176087123246
Test MAPE: MAE: | 0.6928 | 0.1827
-------Target city: Perth--------
(72, 12) (72, 1)
Early stopping at epoch: 20
epoch 20 train loss: 0.6606153249740601 validation loss: 1.1877894401550293
Transfer Test MAPE: MAE: | 0.2121 | 0.4225
Early stopping at epoch: 22
epoch 22 train loss: 1.3811805248260498 validation loss: 1.0648589134216309
Wo Transfer Test MAPE:  MAE: | 0.2811  | 0.5891
-------Target city: HK--------
(120, 12) (120, 1)
Early stopping at epoch: 20
epoch 20 train loss: 1.0942175697397303 validation loss: 0.9033480882644653
Transfer Test MAPE: MAE: | 0.2007 | 0.4708
Early stopping at epoch: 22
epoch 22 train loss: 0.6012875437736511 validation loss: 1.5380504131317139
Wo Transfer Test MAPE:  MAE: | 0.2456  | 0.4569
-------Target city: PALO--------
(84, 12) (84, 1)
Early stopping at epoch: 44
epoch 44 train loss: 0.9038211107254028 validation loss: 1.5857539176940918
Transfer T

Early stopping at epoch: 27
epoch 27 train loss: 0.9247285174543952 validation loss: 0.9248761534690857
Test MAPE: MAE: | 0.8676 | 0.4575
-------Target city: Perth--------
(72, 12) (72, 1)
Early stopping at epoch: 23
epoch 23 train loss: 0.6603531241416931 validation loss: 1.1747938394546509
Transfer Test MAPE: MAE: | 0.2121 | 0.4225
Early stopping at epoch: 22
epoch 22 train loss: 1.3811805248260498 validation loss: 1.0648589134216309
Wo Transfer Test MAPE:  MAE: | 0.2811  | 0.5891
-------Target city: HK--------
(120, 12) (120, 1)
Early stopping at epoch: 20
epoch 20 train loss: 1.0934211310045219 validation loss: 0.8995388746261597
Transfer Test MAPE: MAE: | 0.2007 | 0.4708
Early stopping at epoch: 22
epoch 22 train loss: 0.6012875437736511 validation loss: 1.5380504131317139
Wo Transfer Test MAPE:  MAE: | 0.2456  | 0.4569
-------Target city: PALO--------
(84, 12) (84, 1)
Early stopping at epoch: 48
epoch 48 train loss: 0.9018677473068237 validation loss: 1.5675737857818604
Transfer 

Early stopping at epoch: 23
epoch 23 train loss: 1.1332756280899048 validation loss: 0.260111004114151
Test MAPE: MAE: | 0.1000 | 0.0590
-------Target city: Perth--------
(72, 12) (72, 1)
Early stopping at epoch: 49
epoch 49 train loss: 0.6640607714653015 validation loss: 1.1789231300354004
Transfer Test MAPE: MAE: | 0.2115 | 0.4213
Early stopping at epoch: 22
epoch 22 train loss: 1.3811805248260498 validation loss: 1.0648589134216309
Wo Transfer Test MAPE:  MAE: | 0.2811  | 0.5891
-------Target city: HK--------
(120, 12) (120, 1)
Early stopping at epoch: 20
epoch 20 train loss: 1.0933024603643535 validation loss: 0.9096550345420837
Transfer Test MAPE: MAE: | 0.2007 | 0.4708
Early stopping at epoch: 22
epoch 22 train loss: 0.6012875437736511 validation loss: 1.5380504131317139
Wo Transfer Test MAPE:  MAE: | 0.2456  | 0.4569
-------Target city: PALO--------
(84, 12) (84, 1)
Early stopping at epoch: 47
epoch 47 train loss: 0.9013941884040833 validation loss: 1.581283688545227
Transfer Te

...

Wo Transfer Test MAPE:  MAE: | 0.5000  | 0.1875
-------Target city: Blairgowrie--------
(540, 12) (540, 1)
Transfer Test MAPE: MAE: | 1.0000 | 0.3333
Wo Transfer Test MAPE:  MAE: | 0.5417  | 0.2569
-------------------------------
-------Source city: Auchterarder-------
-------------------------------
(564, 12) (564, 1)
Test MAPE: MAE: | 1.0000 | 0.2153
-------Target city: Perth--------
(3240, 12) (3240, 1)
Transfer Test MAPE: MAE: | 0.2034 | 0.3542
Wo Transfer Test MAPE:  MAE: | 0.1944  | 0.3692
-------Target city: HK--------
(5400, 12) (5400, 1)
Transfer Test MAPE: MAE: | 0.2133 | 0.4583
Wo Transfer Test MAPE:  MAE: | 0.2411  | 0.4840
-------Target city: PALO--------
(3780, 12) (3780, 1)
Transfer Test MAPE: MAE: | 0.2547 | 0.8690
Wo Transfer Test MAPE:  MAE: | 0.4460  | 0.7341
-------Target city: DUNDEE--------
(14580, 12) (14580, 1)
Transfer Test MAPE: MAE: | 0.2347 | 0.3945
Wo Transfer Test MAPE:  MAE: | 0.2032  | 0.3830
-------Target city: BOULDER--------
(10260, 12) (10260, 1)
Tra

Wo Transfer Test MAPE:  MAE: | 0.4516  | 0.2153
-------Target city: Kinross--------
(4320, 12) (4320, 1)
Transfer Test MAPE: MAE: | 1.0000 | 0.4132
Wo Transfer Test MAPE:  MAE: | 0.8550  | 0.4227
-------Target city: Pitlochry--------
(1620, 12) (1620, 1)
Transfer Test MAPE: MAE: | 0.3110 | 0.1505
Wo Transfer Test MAPE:  MAE: | 0.3110  | 0.1574
-------Target city: Crieff--------
(1080, 12) (1080, 1)
Transfer Test MAPE: MAE: | 0.1000 | 0.0556
Wo Transfer Test MAPE:  MAE: | 0.0437  | 0.0417
-------Target city: Dunkeld--------
(540, 12) (540, 1)
Transfer Test MAPE: MAE: | 1.0000 | 0.2361
Wo Transfer Test MAPE:  MAE: | 0.5000  | 0.1875
-------Target city: Blairgowrie--------
(540, 12) (540, 1)
Transfer Test MAPE: MAE: | 1.0000 | 0.3333
Wo Transfer Test MAPE:  MAE: | 0.5417  | 0.2569
-------------------------------
-------Source city: Dunkeld-------
-------------------------------
(564, 12) (564, 1)
Test MAPE: MAE: | 1.0000 | 0.2361
-------Target city: Perth--------
(3240, 12) (3240, 1)
Tran

Wo Transfer Test MAPE:  MAE: | 0.2463  | 0.4861
-------Target city: DUNDEE--------
(15228, 12) (15228, 1)
Transfer Test MAPE: MAE: | 0.2347 | 0.3945
Wo Transfer Test MAPE:  MAE: | 0.2080  | 0.3890
-------Target city: BOULDER--------
(10716, 12) (10716, 1)
Transfer Test MAPE: MAE: | 0.6928 | 0.1827
Wo Transfer Test MAPE:  MAE: | 0.6476  | 0.1838
-------Target city: Auchterarder--------
(564, 12) (564, 1)
Transfer Test MAPE: MAE: | 1.0000 | 0.2153
Wo Transfer Test MAPE:  MAE: | 0.5484  | 0.2361
-------Target city: Kinross--------
(4512, 12) (4512, 1)
Transfer Test MAPE: MAE: | 1.0000 | 0.4132
Wo Transfer Test MAPE:  MAE: | 0.8109  | 0.4366
-------Target city: Pitlochry--------
(1692, 12) (1692, 1)
Transfer Test MAPE: MAE: | 0.3110 | 0.1505
Wo Transfer Test MAPE:  MAE: | 0.3110  | 0.1667
-------Target city: Crieff--------
(1128, 12) (1128, 1)
Transfer Test MAPE: MAE: | 0.1000 | 0.0556
Wo Transfer Test MAPE:  MAE: | 0.0437  | 0.0417
-------Target city: Aberfeldy--------
(1128, 12) (1128, 1

Wo Transfer Test MAPE:  MAE: | 0.5000  | 0.1875
-------Target city: Blairgowrie--------
(564, 12) (564, 1)
Transfer Test MAPE: MAE: | 1.0000 | 0.3333
Wo Transfer Test MAPE:  MAE: | 0.5417  | 0.2431
-------------------------------
-------Source city: Pitlochry-------
-------------------------------
(1692, 12) (1692, 1)
Test MAPE: MAE: | 0.3110 | 0.1505
-------Target city: Perth--------
(3384, 12) (3384, 1)
Transfer Test MAPE: MAE: | 0.2034 | 0.3542
Wo Transfer Test MAPE:  MAE: | 0.1943  | 0.3762
-------Target city: HK--------
(5640, 12) (5640, 1)
Transfer Test MAPE: MAE: | 0.2133 | 0.4583
Wo Transfer Test MAPE:  MAE: | 0.2463  | 0.4861
-------Target city: PALO--------
(3948, 12) (3948, 1)
Transfer Test MAPE: MAE: | 0.2547 | 0.8690
Wo Transfer Test MAPE:  MAE: | 0.4898  | 0.7312
-------Target city: DUNDEE--------
(15228, 12) (15228, 1)
Transfer Test MAPE: MAE: | 0.2347 | 0.3945
Wo Transfer Test MAPE:  MAE: | 0.2080  | 0.3890
-------Target city: BOULDER--------
(10716, 12) (10716, 1)
Tran

Wo Transfer Test MAPE:  MAE: | 0.5484  | 0.2361
-------Target city: Kinross--------
(4512, 12) (4512, 1)
Transfer Test MAPE: MAE: | 1.0000 | 0.4132
Wo Transfer Test MAPE:  MAE: | 0.8109  | 0.4366
-------Target city: Pitlochry--------
(1692, 12) (1692, 1)
Transfer Test MAPE: MAE: | 0.3110 | 0.1505
Wo Transfer Test MAPE:  MAE: | 0.3110  | 0.1667
-------Target city: Crieff--------
(1128, 12) (1128, 1)
Transfer Test MAPE: MAE: | 0.1000 | 0.0556
Wo Transfer Test MAPE:  MAE: | 0.0437  | 0.0417
-------Target city: Aberfeldy--------
(1128, 12) (1128, 1)
Transfer Test MAPE: MAE: | 0.0710 | 0.0382
Wo Transfer Test MAPE:  MAE: | 0.0323  | 0.0243
-------Target city: Dunkeld--------
(564, 12) (564, 1)
Transfer Test MAPE: MAE: | 1.0000 | 0.2361
Wo Transfer Test MAPE:  MAE: | 0.5000  | 0.1875
